In [ ]:
import numpy as np
import pandas as pd
import geopandas as gpd

import argparse
import sys, os
import sklearn
import datetime

import importlib
from tqdm import tqdm
from joblib import Parallel, delayed

import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.preprocessing import MinMaxScaler, StandardScaler

from sklearn.metrics import mean_absolute_error, mean_squared_error, mean_squared_log_error, mean_absolute_percentage_error
from sklearn.pipeline import make_pipeline

from sklearn.ensemble import RandomForestRegressor
from sklearn_rvm import EMRVR
from sklearn.svm import SVR

from sklearn.neural_network import MLPRegressor
pd.set_option('display.max_columns', None)

In [ ]:
def split(X, y, train_size=0.65, validate_size=0.15, test_size=0.2, random_state=None):

    assert train_size + validate_size + test_size == 1, "Train, validate, and test sizes must sum to 1"

    X_train, X_temp, y_train, y_temp = train_test_split(X, y, train_size=train_size, random_state=random_state)

    validate_size_temp = validate_size / (validate_size + test_size)

    X_validate, X_test, y_validate, y_test = train_test_split(X_temp, y_temp, train_size=validate_size_temp, random_state=random_state)

    # Return indices
    train_index = X_train.index
    validate_index = X_validate.index
    test_index = X_test.index

    return train_index, validate_index, test_index

# (X_train, y_train), (X_validate, y_validate), (X_test, y_test) = split(X, y, random_state=42)

In [ ]:
def evaluate_clf(clf, X, y, train_index, validate_index, test_index, include_indices=False):
    print(f'Training with {len(train_index)} samples; Validating with {len(validate_index)} samples; Testing with {len(test_index)} samples')

    # Get Train/Validate/Test Sets
    X_train, X_validate, X_test = X.iloc[train_index].values, X.iloc[validate_index].values, X.iloc[test_index].values
    y_train, y_validate, y_test = y.iloc[train_index].values, y.iloc[validate_index].values, y.iloc[test_index].values

    # Train Model on Training Set
    clf.fit(X_train, y_train)
    y_pred_validate = clf.predict(X_validate)
    y_pred_test = clf.predict(X_test)

    # Organize and Return Results
    result = dict(
        instance = clf,
        X_train=X_train,
        X_validate=X_validate,
        X_test=X_test,
        y_train = y_train,
        y_true_validate = y_validate,
        y_true_test = y_test,
        y_pred_validate = y_pred_validate,
        y_pred_test = y_pred_test,
        acc_validate = clf.score(X_validate, y_validate),
        acc_test = clf.score(X_test, y_test),
        mae_validate = mean_absolute_error(y_validate, y_pred_validate),
        mae_test = mean_absolute_error(y_test, y_pred_test),
        rmse_validate = mean_squared_error(y_validate, y_pred_validate, squared=False),
        rmse_test = mean_squared_error(y_test, y_pred_test, squared=False),
        rmsle_validate = mean_squared_log_error(y_validate, y_pred_validate, squared=False),
        rmsle_test = mean_squared_log_error(y_test, y_pred_test, squared=False),
    )

    if include_indices:
        result.update({
            'train_indices':train_index,
            'validate_indices':validate_index,
            'test_indices':test_index
        })

    return result

In [ ]:
def evaluate_clf2(clf, X, y, train_index, validate_index, test_index, include_indices=False):
    print(f'Training with {len(train_index)} samples; Validating with {len(validate_index)} samples; Testing with {len(test_index)} samples')

    # Ensure y is a 1D array
    if isinstance(y, pd.DataFrame):
        y = y.values.ravel()
    elif isinstance(y, pd.Series):
        y = y.values

    # Get Train/Validate/Test Sets
    X_train, X_validate, X_test = X.iloc[train_index].values, X.iloc[validate_index].values, X.iloc[test_index].values
    y_train, y_validate, y_test = y[train_index], y[validate_index], y[test_index]

    # Train Model on Training Set
    clf.fit(X_train, y_train)
    y_pred_validate = clf.predict(X_validate)
    y_pred_test = clf.predict(X_test)

    # Organize and Return Results
    result = dict(
        instance = clf,
        X_train=X_train,
        X_validate=X_validate,
        X_test=X_test,
        y_train = y_train,
        y_true_validate = y_validate,
        y_true_test = y_test,
        y_pred_validate = y_pred_validate,
        y_pred_test = y_pred_test,
        acc_validate = clf.score(X_validate, y_validate),
        acc_test = clf.score(X_test, y_test),
        mae_validate = mean_absolute_error(y_validate, y_pred_validate),
        mae_test = mean_absolute_error(y_test, y_pred_test),
        rmse_validate = mean_squared_error(y_validate, y_pred_validate, squared=False),
        rmse_test = mean_squared_error(y_test, y_pred_test, squared=False),
        rmsle_validate = mean_squared_log_error(y_validate, y_pred_validate, squared=False),
        rmsle_test = mean_squared_log_error(y_test, y_pred_test, squared=False),
    )

    if include_indices:
        result.update({
            'train_indices':train_index,
            'validate_indices':validate_index,
            'test_indices':test_index
        })

    return result

In [ ]:
X = pd.read_pickle('Final\\X_df.pkl')

In [ ]:
X

dist_euclid  own_speed  target_speed  own_course  target_course
0         10.655910   9.827940      1.206454  109.262214     167.395637
1          3.116042   9.827940     38.151892  109.262214       7.500070
2         10.655910   1.206454      9.827940  167.395637     109.262214
3         10.479444   1.206454     38.151892  167.395637       7.500070
4          3.116042  38.151892      9.827940    7.500070     109.262214
...             ...        ...           ...         ...            ...
264765     6.178706   1.657704      2.129840  188.961942     219.598516
264766     6.182760   2.129840      1.521905  219.598516      30.599527
264767     6.182760   1.521905      2.129840   30.599527     219.598516
264768    25.225222   1.251172     11.578077  218.256384     100.759199
264769    25.225222  11.578077      1.251172  100.759199     218.256384

[264770 rows x 5 columns]

In [ ]:
y = pd.read_pickle('Final\\y_consequence_df.pkl')

In [ ]:
y

Consequence
0          0.233781
1          0.213215
2          0.233781
3          0.214537
4          0.157967
...             ...
264765     0.302878
264766     0.156704
264767     0.176238
264768     0.222910
264769     0.213215

[264770 rows x 1 columns]

SVM-VCRA (Gang et al.)

In [ ]:
clf = make_pipeline(StandardScaler(), SVR(gamma='auto', kernel='rbf', verbose=True))

svm_vcra_skf_results = Parallel(n_jobs=-1)(delayed(evaluate_clf)(
    clf, X, y, train_index, validate_index, test_index, include_indices=True
)for (train_index, validate_index, test_index) in tqdm([split(X, y, random_state=42)]))

100%|████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 60.43it/s]


In [ ]:
svm_vcra_skf_results

[{'instance': Pipeline(steps=[('standardscaler', StandardScaler()),
                  ('svr', SVR(gamma='auto', verbose=True))]),
  'X_train': array([[  3.05550465,  12.28032958,  13.12811152, 347.91325923,
          247.78601524],
         [  5.40508959,   6.74768908,  38.68803114,  52.60657187,
           52.75311729],
         [ 13.73810957,   3.54080214,  17.71525997,  54.45272988,
          339.29577424],
         ...,
         [  4.90611205,   1.32644532,  12.2262035 , 238.93492277,
          171.38145762],
         [ 17.23531976,  33.07634159,  30.56979075,  26.50342452,
          251.44749052],
         [  4.8616002 ,  13.87401615,   3.30519046, 210.05918927,
          162.49468038]]),
  'X_validate': array([[  7.67863944,  32.26405757,  10.22987534,  40.10745581,
          170.4060249 ],
         [  8.73973488,   1.17747102,   4.36463356, 297.78818941,
           55.85764627],
         [  1.07457517,   2.92157799,  12.08781879, 293.09969984,
          203.2999398 ],
         .

RVM-VCRA (Park et al.)

In [ ]:
clf = make_pipeline(StandardScaler(), EMRVR(kernel='rbf', verbose=True))

In [ ]:
# Reduce dataset size for demonstration
y1 = y.values.ravel()
X_small = X.sample(frac=0.1, random_state=42)
y_small = y1[X_small.index]

X_small = X_small.reset_index()
y_small = pd.Series(y_small).reset_index(drop=True).values

# Assuming split is a function that yields train/validate/test indices
train_index, validate_index, test_index = split(X_small, y_small, random_state=42)

rvm_results = Parallel(n_jobs=1)(delayed(evaluate_clf2)(
     clf, X_small, y_small, train_index, validate_index, test_index, include_indices=True
)for _ in tqdm(range(1)))

# Use tqdm to wrap the iterable
# rvm_results = Parallel(n_jobs=1)(delayed(evaluate_clf2)(
#     clf, X_small, y_small, train_index, validate_index, test_index, include_indices=True
# )) for (train_index, validate_index, test_index) in tqdm(indices))

  0%|                                                                                            | 0/1 [00:00<?, ?it/s]

Training with 17210 samples; Validating with 3971 samples; Testing with 5296 samples


C:\Users\kka\AppData\Roaming\Python\Python311\site-packages\sklearn_rvm\em_rvm.py:324: UserWarning: Hessian not positive definite
  warnings.warn("Hessian not positive definite")


Iteration: 0
Alpha: [1.40453873e-05 1.00198251e-08 1.09458093e-08 ... 1.44978961e-08
 1.02799796e-08 1.04308740e-08]
Beta: 2.5499719395862803e-07
Gamma: [0.99999997 1.00291879 1.00034526 ... 0.99683113 1.00095904 1.00073194]
mu: [   -266.92410325 -224918.51469142   32521.69424259 ...   14886.96217286
  -59792.25540958  -48192.9767468 ]
Relevance Vectors: 17210

Iteration: 1
Alpha: [209.21544909   3.33006003   3.16483872 ...  11.01608595 226.69523424
   8.8266487 ]
Beta: 53.56072934939458
Gamma: [0.02602469 0.01769649 0.08144072 ... 0.01638561 0.02481921 0.05020227]
mu: [ 0.01115311 -0.07289832  0.16041501 ...  0.03856716  0.0104634
 -0.07541605]
Relevance Vectors: 17210

Iteration: 2
Alpha: [  43.4835108     6.03378411   14.72246775 ...  383.77641361 4339.44430322
   50.83495268]
Beta: 53.92935220765704
Gamma: [0.44364278 0.02847469 0.15716998 ... 0.01657489 0.00071763 0.04960598]
mu: [ 0.10100768 -0.0686965   0.1033224  ...  0.00657183  0.00040666
 -0.03123819]
Relevance Vectors: 1720

100%|██████████████████████████████████████████████████████████████████████████████████| 1/1 [29:16<00:00, 1756.67s/it]

Iteration: 623
Alpha: [9.34394043e+00 6.66622150e-02 9.34687386e-01 7.92340233e-02
 9.06963191e-01 9.33591941e-01 3.01459702e+01 3.01081007e+00
 5.92726562e-01 2.45763345e+01 3.67318116e-01 2.27912557e-01
 4.54040806e-01 2.20871027e-01 3.54631223e+00 2.31539155e+01
 7.27810435e+00 8.69844884e+00 1.66380924e+00 5.21172758e-01
 8.14812703e+01 6.17052038e-02 9.21332088e-01 5.27207690e-01
 1.86371295e+01 4.29609401e+00 1.74123521e+00 6.78542892e+02
 1.11217482e-01 1.70878362e-01 2.18101721e-01 5.43287386e-01
 2.63736293e+01 7.40132274e-02 9.12987736e-02 7.29877798e-01
 1.23263558e+00 1.11621663e-01 5.29189571e-01 1.18373242e-01
 1.62278706e-01 2.97193395e-01 4.44026041e+00 4.44980827e-02
 7.54148024e+00 3.60349427e+00 3.18066091e+01 3.61314307e+01
 3.30668966e-01 3.79435470e+00 6.22840868e-01 1.62156392e+01
 1.43467388e-01 7.75605180e-01 2.88441963e+00 7.36045986e-02
 3.27396572e-01 1.03090662e+00 2.49157430e+01 1.32013719e+00
 1.83293962e-01 5.95462205e-01 1.34523305e+01 3.91364507e+00
 4

In [ ]:
rvm_results

[{'instance': Pipeline(steps=[('standardscaler', StandardScaler()),
                  ('emrvr',
                   EMRVR(init_alpha=3.3758861418391862e-09, verbose=True))]),
  'X_train': array([[1.79005000e+05, 1.96132016e+00, 5.61324391e+00, 9.80139417e+00,
          3.20063024e+02, 7.61781900e+01],
         [2.57986000e+05, 8.89562347e+00, 1.12284228e+01, 2.56679288e+01,
          2.34725565e+02, 3.37864168e+02],
         [2.22186000e+05, 5.56984064e+00, 6.22730777e+00, 2.33263482e+00,
          1.22941198e+02, 1.94579628e+02],
         ...,
         [1.77291000e+05, 1.48554957e+01, 1.07101659e+01, 8.39764060e+00,
          3.09723117e+02, 1.55133997e+02],
         [2.67860000e+04, 3.68868685e+00, 1.20175812e+01, 1.60931074e+00,
          1.88816488e+02, 2.33961335e+01],
         [1.43796000e+05, 1.22290600e+01, 2.29586907e+01, 1.29110242e+00,
          1.41678610e+02, 8.19805078e+01]]),
  'X_validate': array([[1.01601000e+05, 1.59305848e+01, 2.00576473e+01, 6.98282707e+00,
         

MLP VCRA (Tritsarolis et al.)

In [ ]:
mlp = make_pipeline(
    StandardScaler(),
    MLPRegressor(random_state=42, max_iter=100, hidden_layer_sizes=(256, 32),
                 verbose=True, early_stopping=True, n_iter_no_change=10)
)

In [ ]:
mlp_results = Parallel(n_jobs=-1)(delayed(evaluate_clf)(
    mlp, X, y, train_index, validate_index, test_index, include_indices=True
)for (train_index, validate_index, test_index) in tqdm([split(X, y, random_state=42)]))

100%|█████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 66.94it/s]


In [ ]:
mlp_results

[{'instance': Pipeline(steps=[('standardscaler', StandardScaler()),
                  ('mlpregressor',
                   MLPRegressor(early_stopping=True, hidden_layer_sizes=(256, 32),
                                max_iter=100, random_state=42, verbose=True))]),
  'X_train': array([[  3.05550465,  12.28032958,  13.12811152, 347.91325923,
          247.78601524],
         [  5.40508959,   6.74768908,  38.68803114,  52.60657187,
           52.75311729],
         [ 13.73810957,   3.54080214,  17.71525997,  54.45272988,
          339.29577424],
         ...,
         [  4.90611205,   1.32644532,  12.2262035 , 238.93492277,
          171.38145762],
         [ 17.23531976,  33.07634159,  30.56979075,  26.50342452,
          251.44749052],
         [  4.8616002 ,  13.87401615,   3.30519046, 210.05918927,
          162.49468038]]),
  'X_validate': array([[  7.67863944,  32.26405757,  10.22987534,  40.10745581,
          170.4060249 ],
         [  8.73973488,   1.17747102,   4.36463356, 297

Combining Results to a Unified DataFrame

In [ ]:
results = [
    {'Regressor': 'SVM', 'ACC': svm_vcra_skf_results[0]['acc_test'], 'MAE': svm_vcra_skf_results[0]['mae_test'], 'RMSE': svm_vcra_skf_results[0]['rmse_test'], 'RMSLE': svm_vcra_skf_results[0]['rmsle_test']},
    {'Regressor': 'RVM', 'ACC': rvm_results[0]['acc_test'], 'MAE': rvm_results[0]['mae_test'], 'RMSE': rvm_results[0]['rmse_test'], 'RMSLE': rvm_results[0]['rmsle_test']},
    {'Regressor': 'MLP', 'ACC': mlp_results[0]['acc_test'], 'MAE': mlp_results[0]['mae_test'], 'RMSE': mlp_results[0]['rmse_test'], 'RMSLE': mlp_results[0]['rmsle_test']}
]
results_df = pd.DataFrame(results)

In [ ]:
results_df

Regressor       ACC       MAE      RMSE     RMSLE
0       SVM  0.197908  0.097694  0.141997  0.103949
1       RVM  0.215571  0.097202  0.140959  0.103811
2       MLP  0.295371  0.090664  0.133091  0.098032

In [ ]:
svm_df = pd.DataFrame(svm_vcra_skf_results)
rvm_df = pd.DataFrame(rvm_results)
mlp_df = pd.DataFrame(mlp_results)

In [ ]:
skf_results_df = pd.concat({
    'svm_vcra': svm_df,
    'rvm_vcra': rvm_df,
    'mlp_vcra': mlp_df
}, names=['model'])

In [ ]:
skf_results_df

instance  \
model                                                           
svm_vcra 0  (StandardScaler(), SVR(gamma='auto', verbose=T...   
rvm_vcra 0  (StandardScaler(), EMRVR(init_alpha=3.37588614...   
mlp_vcra 0  (StandardScaler(), MLPRegressor(early_stopping...   

                                                      X_train  \
model                                                           
svm_vcra 0  [[3.0555046538777093, 12.280329582748491, 13.1...   
rvm_vcra 0  [[179005.0, 1.961320159757827, 5.6132439061296...   
mlp_vcra 0  [[3.0555046538777093, 12.280329582748491, 13.1...   

                                                   X_validate  \
model                                                           
svm_vcra 0  [[7.678639438526909, 32.264057573069735, 10.22...   
rvm_vcra 0  [[101601.0, 15.930584771106691, 20.05764727424...   
mlp_vcra 0  [[7.678639438526909, 32.264057573069735, 10.22...   

                                                       X_test  \
model                                                           
svm_vcra 0  [[2.912215887008789, 5.051411546683967, 32.648...   
rvm_vcra 0  [[236575.0, 13.510264896115547, 14.97570534696...   
mlp_vcra 0  [[2.912215887008789, 5.051411546683967, 32.648...   

                                                      y_train  \
model                                                           
svm_vcra 0  [[0.19498130357213764], [0.3088163472180326], ...   
rvm_vcra 0  [0.11954646850877715, 0.25293443591520376, 0.6...   
mlp_vcra 0  [[0.19498130357213764], [0.3088163472180326], ...   

                                              y_true_validate  \
model                                                           
svm_vcra 0  [[0.18842943816498522], [0.24450164405918898],...   
rvm_vcra 0  [0.18842943816498522, 0.744104253805213, 0.112...   
mlp_vcra 0  [[0.18842943816498522], [0.24450164405918898],...   

                                                  y_true_test  \
model                                                           
svm_vcra 0  [[0.2137883840472583], [0.27800550199494095], ...   
rvm_vcra 0  [0.1146001870060352, 0.15796744511169059, 0.11...   
mlp_vcra 0  [[0.2137883840472583], [0.27800550199494095], ...   

                                              y_pred_validate  \
model                                                           
svm_vcra 0  [0.21597490616792586, 0.2045497867750234, 0.23...   
rvm_vcra 0  [0.1298844631966043, 0.35772209160656576, 0.15...   
mlp_vcra 0  [0.18868662812720233, 0.1799402616822094, 0.27...   

                                                  y_pred_test  acc_validate  \
model                                                                         
svm_vcra 0  [0.332669809693722, 0.19870968211644596, 0.216...      0.198935   
rvm_vcra 0  [0.154234141192374, 0.1977744151817955, 0.1734...      0.212083   
mlp_vcra 0  [0.3234025898678815, 0.22031648653980102, 0.22...      0.294339   

            acc_test  mae_validate  mae_test  rmse_validate  rmse_test  \
model                                                                    
svm_vcra 0  0.197908      0.096795  0.097694       0.140852   0.141997   
rvm_vcra 0  0.215571      0.095662  0.097202       0.140234   0.140959   
mlp_vcra 0  0.295371      0.090145  0.090664       0.132198   0.133091   

            rmsle_validate  rmsle_test  \
model                                    
svm_vcra 0        0.103163    0.103949   
rvm_vcra 0        0.103152    0.103811   
mlp_vcra 0        0.097476    0.098032   

                                                train_indices  \
model                                                           
svm_vcra 0  Int64Index([170889,  59840, 205039, 254150,  2...   
rvm_vcra 0  Int64Index([ 6369,  1038,  7931, 23998, 25964,...   
mlp_vcra 0  Int64Index([170889,  59840, 205039, 254150,  2...   

                                             validate_indices  \
model                                                           
svm_vcra 0 

In [ ]:
skf_results_df.loc[:, 'r2_score'] = skf_results_df.apply(lambda l: sklearn.metrics.r2_score(l.y_true_test, l.y_pred_test), axis=1)

In [ ]:
skf_results_df.groupby(level=0, sort=False).mean(numeric_only=True)

acc_validate  acc_test  mae_validate  mae_test  rmse_validate  \
model                                                                     
svm_vcra      0.198935  0.197908      0.096795  0.097694       0.140852   
rvm_vcra      0.212083  0.215571      0.095662  0.097202       0.140234   
mlp_vcra      0.294339  0.295371      0.090145  0.090664       0.132198   

          rmse_test  rmsle_validate  rmsle_test  r2_score  
model                                                      
svm_vcra   0.141997        0.103163    0.103949  0.197908  
rvm_vcra   0.140959        0.103152    0.103811  0.215571  
mlp_vcra   0.133091        0.097476    0.098032  0.295371

In [ ]:
bins=np.arange(0, 1.1, .2)

In [ ]:
def metrics_per_cri_pct(sdf):
    # Ensure y_true is 1-dimensional
    y_true = sdf.y_true_test.flatten() if sdf.y_true_test.ndim > 1 else sdf.y_true_test
    buckets = pd.cut(y_true, bins, right=True, include_lowest=True)
    return pd.DataFrame({'y_true': y_true, 'y_pred': sdf.y_pred_test}).groupby(buckets).apply(
        lambda l: mean_squared_log_error(l.y_true, l.y_pred, squared=False)
    )

skf_results_df.apply(
    lambda l: metrics_per_cri_pct(l),
    axis=1
).groupby(level=0).mean()

(-0.001, 0.2]  (0.2, 0.4]  (0.4, 0.6]  (0.6, 0.8]  (0.8, 1.0]
model                                                                  
mlp_vcra       0.088800    0.048503    0.192662    0.204089    0.208778
rvm_vcra       0.092988    0.047389    0.203613    0.221580    0.244922
svm_vcra       0.085177    0.046270    0.205214    0.245507    0.247088

In [ ]:
Out[40].columns = ['[0, 0.2]', '(0.2, 0.4]', '(0.4, 0.6]', '(0.6, 0.8]', '(0.8, 1.0]']
Out[40]

[0, 0.2]  (0.2, 0.4]  (0.4, 0.6]  (0.6, 0.8]  (0.8, 1.0]
model                                                             
mlp_vcra  0.088800    0.048503    0.192662    0.204089    0.208778
rvm_vcra  0.092988    0.047389    0.203613    0.221580    0.244922
svm_vcra  0.085177    0.046270    0.205214    0.245507    0.247088